# Imports

In [1]:
# General Imports
import gc
import sys
import pickle
from models_utils import *
from amino_acid_features import sanity_check_dimensions
from tqdm import tqdm

# PyTorch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import WeightedRandomSampler

# PyTorch Geometric
import torch_geometric
from torch_geometric.data.dataset import Dataset
from torch_geometric.nn import GCNConv, global_mean_pool

# Sets the seed for generating random numbers in PyTorch, numpy and Python.
torch_geometric.seed_everything(42)
dtype = torch.float

if torch.cuda.is_available():
    gc.collect()
    torch.cuda.empty_cache()

    device = torch.device("cuda")
    current_device = torch.cuda.current_device()

    print(f"Device Name: {torch.cuda.get_device_name(current_device)}")
    print(f"Device Available: {torch.cuda.is_available()}")
    print(f"Device Initialised: {torch.cuda.is_initialized()}")
    print(f"Device Properties: {torch.cuda.get_device_properties(current_device)}")
    print(f"Device Memory Summary: \n {torch.cuda.memory_summary(current_device)}")
    os.environ['CUDA_LAUNCH_BLOCKING'] = "1"
    os.environ["PYTORCH_CUDA_ALLOC_CONF"] = 'max_split_size_mb:512'
else:
    device = torch.device("cpu")

Intel(R) Extension for Scikit-learn* enabled (https://github.com/intel/scikit-learn-intelex)


Device Name: NVIDIA GeForce GTX 1050 Ti
Device Available: True
Device Initialised: True
Device Properties: _CudaDeviceProperties(name='NVIDIA GeForce GTX 1050 Ti', major=6, minor=1, total_memory=4095MB, multi_processor_count=6)
Device Memory Summary: 
 |===========================================================================|
|                  PyTorch CUDA memory summary, device ID 0                 |
|---------------------------------------------------------------------------|
|            CUDA OOMs: 0            |        cudaMalloc retries: 0         |
|===========================================================================|
|        Metric         | Cur Usage  | Peak Usage | Tot Alloc  | Tot Freed  |
|---------------------------------------------------------------------------|
| Allocated memory      |       0 B  |       0 B  |       0 B  |       0 B  |
|       from large pool |       0 B  |       0 B  |       0 B  |       0 B  |
|       from small pool |       0 B  |       

In [2]:
print(f"Python Version: {sys.version}")
print(f"Torch Version: {torch.__version__}")
print(f"Cuda Version: {torch.version.cuda}")
print(f"Torch Geometric Version: {torch_geometric.__version__}")

Python Version: 3.9.16 (main, Jan 11 2023, 16:16:36) [MSC v.1916 64 bit (AMD64)]
Torch Version: 1.13.0
Cuda Version: 11.7
Torch Geometric Version: 2.1.0


# Helper Methods

In [3]:
def print_useful_information(dataframe):
    binding_count = dataframe[dataframe['Molecular_Function_DNA.binding'] == 1]
    non_binding_count = dataframe[dataframe['Molecular_Function_DNA.binding'] == 0]

    print(f"DNA Binding Count: {binding_count.shape[0]}")
    print(f"DNA Non-Binding Count: {non_binding_count.shape[0]}")
    print(f"Class Imbalance: {non_binding_count.shape[0] / binding_count.shape[0]:.0f}:1 (DNA Non-Binding:DNA Binding)")

In [4]:
def remove_proteins_with_no_graphs(dataframe, dataframe_name):
    proteins_with_no_graphs = np.load("../Dataset_Files/Protein_Graph_Data/proteins_with_no_graphs.npy")

    dataframe_correct_dimensions = dataframe[dataframe["Protein_Accession"].isin(proteins_with_no_graphs) == False]
    dataframe_correct_dimensions.reset_index(inplace=True, drop=True)

    size_difference = len(dataframe) - len(dataframe_correct_dimensions)

    print(f"{dataframe_name} entries lost due to wrong graphs: {size_difference}")
    return dataframe_correct_dimensions

In [5]:
def get_dataset():
    dataset_feature_selection = load_from_pickle("Dataset_Populated_Feature_Selection")

    dataset_feature_selection_correct_dimensions = remove_proteins_with_no_graphs(dataset_feature_selection, "Training")

    protein_accession_class = dataset_feature_selection_correct_dimensions.loc[:,
                              "Protein_Accession":"Molecular_Function_DNA.binding"]

    X_normalised = normalise(dataset_feature_selection_correct_dimensions, "hydrophobicity.Group1")
    X_normalised = pd.DataFrame(X_normalised,
                                columns=dataset_feature_selection_correct_dimensions.loc[0,
                                        "hydrophobicity.Group1":].index,
                                index=protein_accession_class.index)

    dataset_normalised_feature_selection_correct_dimensions = pd.concat([protein_accession_class, X_normalised], axis=1)
    print_useful_information(dataset_normalised_feature_selection_correct_dimensions)
    return dataset_normalised_feature_selection_correct_dimensions

# Dataframe

In [6]:
dataframe = get_dataset()
dataframe

Training entries lost due to wrong graphs: 168
DNA Binding Count: 1989
DNA Non-Binding Count: 9045
Class Imbalance: 5:1 (DNA Non-Binding:DNA Binding)


Protein_Accession  Molecular_Function_DNA.binding  \
0            A0A024RBG1                               0   
1            A0A075B6L2                               0   
2            A0A075B6L6                               0   
3            A0A075B6N1                               0   
4            A0A075B6N2                               0   
...                 ...                             ...   
11029            Q9Y6X6                               0   
11030            Q9Y6X8                               1   
11031            Q9Y6X9                               0   
11032            Q9Y6Y1                               0   
11033            U3KPV4                               0   

       hydrophobicity.Group1  hydrophobicity.Group3  polarity.Group1  \
0                   0.916405              -0.305236        -0.233445   
1                  -0.735651               0.981135         0.850915   
2                  -0.591904              -0.581802        -0.467647   
3                   0.141412               0.139337         0.592398   
4                  -1.295328               0.553585         0.478548   
...                      ...                    ...              ...   
11029               0.152197              -0.227904        -0.267759   
11030               0.571363              -0.947613        -1.019462   
11031               1.295959              -0.660280        -0.680386   
11032              -0.183990              -0.665566        -0.660520   
11033              -0.762314               0.489511         0.367885   

       polarity.Group3  charge.Group1  secondarystruct.Group2  \
0             0.731093       0.642717               -0.000319   
1            -0.366682       0.039038                1.244539   
2            -0.741001      -0.353082               -0.228781   
3            -0.153705      -0.843365                0.887530   
4            -1.282997      -0.773463                0.246857   
...                ...            ...                     ...   
11029         0.165412      -0.271806               -0.800540   
11030         0.505742       0.198593               -0.251205   
11031         1.057755       1.312932               -0.317940   
11032        -0.116283      -0.433691               -0.321995   
11033        -0.537294       0.039038               -0.318540   

       solventaccess.Group1  solventaccess.Group2     Xc1.Q     Xc1.K  \
0                 -0.214877              0.916405 -0.792135 -0.701142   
1                  0.790031             -0.735651 -0.852348 -0.702965   
2                  0.773383             -0.591904 -0.825111 -0.949516   
3                 -0.016122              0.141412 -0.684033 -0.902643   
4                  0.169075             -1.295328 -0.837127 -0.891074   
...                     ...                   ...       ...       ...   
11029             -0.439321              0.152197  2.725410  2.775455   
11030             -1.035372              0.571363  1.001802  1.263062   
11031             -1.112525              1.295959  0.774422  1.448333   
11032             -0.798424             -0.183990  3.101483  2.268052   
11033              1.364416             -0.762314 -0.671214 -0.846748   

       UniProt_Embedding_24  UniProt_Embedding_33  UniProt_Embedding_36  \
0                  0.298237             -0.565300             -1.991293   
1                 -0.658022             -0.286108              0.497560   
2                 -0.433889             -0.153859              1.072179   
3                  0.894354             -0.158757              0.904891   
4                  0.074740             -0.173451              0.386035   
...                     ...                   ...                   ...   
11029              0.453920             -0.682855              0.365559   
11030             -0.183777             -1.015926             -1.447605   
11031              1.190057             -0.315496             -0.858174   
11032              0.651

# Contact Maps Loading & Plotting

In [7]:
contact_map_A0A0A0MRZ7 = np.load("../Dataset_Files/Protein_Graph_Data/raw/Contact_Map_Files/A0A0A0MRZ7.npy")
fig = px.imshow(contact_map_A0A0A0MRZ7, color_continuous_scale=["white", "black"], template=template)

fig.show()

# Dataset Class

In [8]:
class MyDataset(Dataset):
    def __init__(self, root, dataframe, unique_proteins_list=None, transform=None, pre_transform=None,
                 pre_filter=None):
        self.dataframe = dataframe
        self.unique_proteins_list = unique_proteins_list
        super(MyDataset, self).__init__(root, transform, pre_transform, pre_filter)

    @property
    def raw_file_names(self):
        return os.listdir(f"{self.root}/raw")

    @property
    def processed_file_names(self):
        return os.listdir(f"{self.root}/processed")

    def download(self):
        pass

    def process(self):
        print("Creating Protein Graphs")
        for i in tqdm(range(len(self.unique_proteins_list))):
            try:
                accession = self.unique_proteins_list[i]

                amino_acid_descriptors = np.load(
                    f"{self.root}/raw/Amino_Acid_Descriptors_And_PSSM/{accession}_Descriptors.npy")
                pssm = np.load(f"{self.root}/raw/Amino_Acid_Descriptors_And_PSSM/{accession}_PSSM.npy")
                uniprot_per_residue_embedding = np.load(f"{self.root}/raw/Amino_Acid_Embeddings/{accession}.npy")
                contact_map = np.load(f"{self.root}/raw/Contact_Map_Files/{accession}.npy")

                if (contact_map.shape[0]) == (amino_acid_descriptors.shape[0]) == (pssm.shape[0]) == (
                        uniprot_per_residue_embedding.shape[0]):
                    amino_acid_features = np.hstack((amino_acid_descriptors, pssm, uniprot_per_residue_embedding))

                    contact_map_sparse = []
                    index_row, index_col = np.where(contact_map == 1)
                    for row, column in zip(index_row, index_col):
                        contact_map_sparse.append([row, column])
                    contact_map_sparse = np.array(contact_map_sparse)

                    data = torch_geometric.data.Data(x=torch.Tensor(amino_acid_features),
                                                     edge_index=torch.LongTensor(contact_map_sparse).transpose(1, 0),
                                                     size=contact_map.shape[0],
                                                     accession=accession)

                    torch.save(data, f"{self.root}/processed/protein_graph_{accession}.pt")
                else:
                    continue

            except:
                continue

    def len(self):
        return self.dataframe.shape[0]

    def get(self, idx):
        accession = self.dataframe.loc[idx, "Protein_Accession"]
        protein_graph = torch.load(f"{self.root}/processed/protein_graph_{accession}.pt")

        protein_sequence_descriptors = torch.tensor(self.dataframe.loc[idx, "hydrophobicity.Group1":],
                                                    dtype=torch.float32)
        label = torch.tensor(self.dataframe.loc[idx, "Molecular_Function_DNA.binding"], dtype=torch.long)

        return protein_sequence_descriptors, protein_graph, label

# Model

In [9]:
class Model(nn.Module):
    def __init__(self, n_output=2, protein_sequence_features=144, amino_acid_features=1110, output_dim=128,
                 dropout=0.2):
        super(Model, self).__init__()

        # Protein Structure Layers
        self.pro_conv1 = GCNConv(amino_acid_features, amino_acid_features)
        self.pro_batch_normalisation1 = nn.BatchNorm1d(amino_acid_features)

        self.pro_conv2 = GCNConv(amino_acid_features, amino_acid_features * 2)
        self.pro_batch_normalisation2 = nn.BatchNorm1d(amino_acid_features * 2)

        self.pro_conv3 = GCNConv(amino_acid_features * 2, amino_acid_features * 4)
        self.pro_batch_normalisation3 = nn.BatchNorm1d(amino_acid_features * 4)

        self.pro_fc1 = nn.Linear(amino_acid_features * 4, 1024)
        self.pro_fc2 = nn.Linear(1024, output_dim)

        # Protein Sequence Descriptors Layers
        self.psd_fc1 = nn.Linear(protein_sequence_features, protein_sequence_features)
        self.psd_batch_normalisation1 = nn.BatchNorm1d(protein_sequence_features)

        self.psd_fc2 = nn.Linear(protein_sequence_features, protein_sequence_features * 2)
        self.psd_batch_normalisation2 = nn.BatchNorm1d(protein_sequence_features * 2)

        self.psd_fc3 = nn.Linear(protein_sequence_features * 2, protein_sequence_features * 4)
        self.psd_batch_normalisation3 = nn.BatchNorm1d(protein_sequence_features * 4)

        self.psd_fc4 = nn.Linear(protein_sequence_features * 4, 1024)
        self.psd_fc5 = nn.Linear(1024, output_dim)

        # Combined Layers
        self.combined_fc1 = nn.Linear(2 * output_dim, 1024)
        self.combined_fc2 = nn.Linear(1024, 512)
        self.out = nn.Linear(512, n_output)

        # Other Layers
        self.relu = nn.ReLU()
        self.dropout = nn.Dropout(dropout)

    def forward(self, protein_sequence_descriptors, protein_graph):
        # Protein Graphs
        x_protein = self.pro_conv1(protein_graph.x, protein_graph.edge_index)
        x_protein = self.relu(x_protein)
        x_protein = self.pro_batch_normalisation1(x_protein)

        x_protein = self.pro_conv2(x_protein, protein_graph.edge_index)
        x_protein = self.relu(x_protein)
        x_protein = self.pro_batch_normalisation2(x_protein)

        x_protein = self.pro_conv3(x_protein, protein_graph.edge_index)
        x_protein = self.relu(x_protein)
        x_protein = self.pro_batch_normalisation3(x_protein)

        x_protein = global_mean_pool(x_protein, protein_graph.batch)

        # Flatten
        x_protein = self.pro_fc1(x_protein)
        x_protein = self.relu(x_protein)
        x_protein = self.dropout(x_protein)

        x_protein = self.pro_fc2(x_protein)
        x_protein = self.dropout(x_protein)

        # Protein Sequence Descriptors
        x_protein_sequence_descriptors = self.psd_fc1(protein_sequence_descriptors)
        x_protein_sequence_descriptors = self.relu(x_protein_sequence_descriptors)
        x_protein_sequence_descriptors = self.psd_batch_normalisation1(x_protein_sequence_descriptors)

        x_protein_sequence_descriptors = self.psd_fc2(x_protein_sequence_descriptors)
        x_protein_sequence_descriptors = self.relu(x_protein_sequence_descriptors)
        x_protein_sequence_descriptors = self.psd_batch_normalisation2(x_protein_sequence_descriptors)

        x_protein_sequence_descriptors = self.psd_fc3(x_protein_sequence_descriptors)
        x_protein_sequence_descriptors = self.relu(x_protein_sequence_descriptors)
        x_protein_sequence_descriptors = self.psd_batch_normalisation3(x_protein_sequence_descriptors)

        x_protein_sequence_descriptors = self.psd_fc4(x_protein_sequence_descriptors)
        x_protein_sequence_descriptors = self.relu(x_protein_sequence_descriptors)
        x_protein_sequence_descriptors = self.dropout(x_protein_sequence_descriptors)

        x_protein_sequence_descriptors = self.psd_fc5(x_protein_sequence_descriptors)
        x_protein_sequence_descriptors = self.dropout(x_protein_sequence_descriptors)

        # Combine
        x_combined = torch.cat((x_protein, x_protein_sequence_descriptors), 1)
        x_combined = self.combined_fc1(x_combined)
        x_combined = self.relu(x_combined)
        x_combined = self.dropout(x_combined)

        x_combined = self.combined_fc2(x_combined)
        x_combined = self.relu(x_combined)
        x_combined = self.dropout(x_combined)
        out = self.out(x_combined)

        return out

# Training Loop

In [10]:
def training_loop(n_epochs, optimizer, model, device, loss_fn, train_loader):
    model = model.to(device)

    train_losses = []
    avg_train_losses = []

    for epoch in range(1, n_epochs + 1):

        # Training
        model.train()
        for protein_sequence_descriptors, protein_graphs, labels in train_loader:
            protein_sequence_descriptors = protein_sequence_descriptors.to(device)
            protein_graphs = protein_graphs.to(device)
            outputs = model(protein_sequence_descriptors, protein_graphs)
            loss = loss_fn(outputs, labels.to(device))

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            train_losses.append(loss.item())

        # Printing Stats
        train_loss = np.average(train_losses)
        avg_train_losses.append(train_loss)

        print(f"[{epoch}:/{n_epochs}] Training Loss: {train_loss:.2f}")

        # Clear lists to track next epoch
        train_losses = []

    torch.save(model.state_dict(), "Dataset_Files/Neural_Networks/mf_model.pt")
    return model, avg_train_losses

# Model Hyperparameters

In [11]:
model = Model()

BATCH_SIZE = 32
N_EPOCHS = 200
LR_RATE = 0.001
WEIGHT_DECAY = 0.0001

optimizer = optim.Adam(model.parameters(), lr=LR_RATE, weight_decay=WEIGHT_DECAY)
loss_fn = nn.CrossEntropyLoss()

# Weighted Random Sampler
To balance our batches, given the clear imbalance between the classes

In [12]:
# Reference
# https://www.maskaravivek.com/post/pytorch-weighted-random-sampler/

training_class_counts = dataframe["Molecular_Function_DNA.binding"].value_counts(ascending=True).to_numpy()

training_weights = 1. / training_class_counts

training_weights_all = np.array([training_weights[t] for t in dataframe["Molecular_Function_DNA.binding"].astype(int)])
training_weights_all = torch.from_numpy(training_weights_all)

print(training_weights)
#print(training_weights_all)
print(len(training_weights_all))

[0.00050277 0.00011056]
11034


# Dataloaders

In [13]:
training_sampler = WeightedRandomSampler(training_weights_all, len(training_weights_all))

trainloader = torch_geometric.loader.DataLoader(
    MyDataset(root="../Dataset_Files/Protein_Graph_Data",
              dataframe=dataframe,
              unique_proteins_list=dataframe.loc[:, "Protein_Accession"]),
    batch_size=BATCH_SIZE,
    sampler=training_sampler)

In [14]:
for protein_sequence_descriptors, protein_graphs, labels in trainloader:
    print(protein_sequence_descriptors.shape)
    print(protein_sequence_descriptors.dtype)
    protein_sequence_descriptors = protein_sequence_descriptors.to(device)
    print(protein_graphs)
    protein_graphs = protein_graphs.to(device)
    print(labels.shape)
    labels = labels.to(device)
    print("Check OK")
    break

torch.Size([32, 144])
torch.float32
DataBatch(x=[18669, 1110], edge_index=[2, 289741], size=[32], accession=[32], batch=[18669], ptr=[33])
torch.Size([32])
Check OK


# Training

In [15]:
# model, train_loss = training_loop(n_epochs=N_EPOCHS,
#                                   optimizer=optimizer,
#                                   model=model,
#                                   device=device,
#                                   loss_fn=loss_fn,
#                                   train_loader=trainloader)
#
# load_to_numpy(train_loss, "Neural_Networks/mf_train_loss")

In [16]:
load_from_numpy("Neural_Networks/mf_train_loss")

array([0.11339996, 0.07785756, 0.0835734 , 0.07071257, 0.0736931 ,
       0.07098129, 0.06006887, 0.06130498, 0.06483565, 0.056689  ,
       0.06247982, 0.05400618, 0.05634175, 0.05724875, 0.06004448,
       0.05764959, 0.05130492, 0.04501449, 0.05616299, 0.0453704 ,
       0.04122233, 0.04674479, 0.04582046, 0.04735578, 0.04336906,
       0.03680433, 0.04174923, 0.03975666, 0.05054074, 0.04216495,
       0.0409558 , 0.03771227, 0.03926447, 0.03598504, 0.04684586,
       0.03512827, 0.03394992, 0.03380969, 0.02796467, 0.03230669,
       0.03106207, 0.03247793, 0.03245615, 0.03524276, 0.02988787,
       0.03032487, 0.02951382, 0.02612126, 0.03039642, 0.03714302,
       0.032536  , 0.03256359, 0.03042663, 0.0277351 , 0.02868623,
       0.03104124, 0.03226861, 0.02589645, 0.02394617, 0.03002077,
       0.022396  , 0.02685013, 0.02325123, 0.03411857, 0.02292241,
       0.025338  , 0.02395948, 0.0255581 , 0.0311159 , 0.02811889,
       0.01993447, 0.02135175, 0.02442882, 0.01988658, 0.02168

In [17]:
train_loss = pd.Series(load_from_numpy("Neural_Networks/mf_train_loss"))

fig = px.line(train_loss,
              labels={
                  "index": "Epoch",
                  "value": "Cross-Entropy Loss",
              },
              title="Cross-Entropy Loss Over Epochs",
              template=template)
fig.update_layout(showlegend=False)
fig.show()

# Get Protein Embeddings

In [20]:
# batch_accession_list = []
# batch_embeddings = []
# protein_embeddings = {}
# model.load_state_dict(torch.load("Dataset_Files/Neural_Networks/mf_model.pt",map_location='cuda:0'))
# model.to(device)

Model(
  (pro_conv1): GCNConv(1110, 1110)
  (pro_batch_normalisation1): BatchNorm1d(1110, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (pro_conv2): GCNConv(1110, 2220)
  (pro_batch_normalisation2): BatchNorm1d(2220, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (pro_conv3): GCNConv(2220, 4440)
  (pro_batch_normalisation3): BatchNorm1d(4440, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (pro_fc1): Linear(in_features=4440, out_features=1024, bias=True)
  (pro_fc2): Linear(in_features=1024, out_features=128, bias=True)
  (psd_fc1): Linear(in_features=144, out_features=144, bias=True)
  (psd_batch_normalisation1): BatchNorm1d(144, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (psd_fc2): Linear(in_features=144, out_features=288, bias=True)
  (psd_batch_normalisation2): BatchNorm1d(288, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (psd_fc3): Linear(in_features=288, out_features=576, bias=Tru

In [ ]:
# # Forward hook
# def get_protein_embeddings():
#     def hook(model, input, output):
#         batch_embeddings.append(output.detach())
#     return hook

In [ ]:
# # Register hook
# hook = model.pro_fc2.register_forward_hook((get_protein_embeddings()))
#
# for protein_sequence_descriptors, protein_graphs, labels in trainloader:
#     gc.collect()
#     torch.cuda.empty_cache()
#
#     output = model(protein_sequence_descriptors.to(device), protein_graphs.to(device))
#
#     for i in range(protein_sequence_descriptors.shape[0]):
#         batch_accession_list.append(protein_graphs[i].accession)
#
#     for i in range(len(batch_accession_list)):
#         protein_embeddings[batch_accession_list[i]] = batch_embeddings[0][i].cpu().numpy()
#
#     batch_accession_list = []
#     batch_embeddings = []
#
# hook.remove()

In [21]:
if os.path.exists("Dataset_Files/protein_embeddings.pkl"):
    with open('Dataset_Files/protein_embeddings.pkl', 'rb') as file:
        protein_embeddings = pickle.load(file)
else:
    with open('Dataset_Files/protein_embeddings.pkl', 'wb') as file:
        pickle.dump(protein_embeddings, file, protocol=pickle.HIGHEST_PROTOCOL)
protein_embeddings

{'Q6JQN1': array([ 1.30066089e-02,  3.88356030e-01, -2.56263018e-02,  2.89109349e-02,
         2.31596529e-01, -2.84079313e-01, -2.70526391e-03,  1.41009502e-02,
        -8.58326256e-02,  1.62036810e-03, -8.80797356e-02, -1.25764245e-02,
         2.64684185e-02, -2.44270731e-02,  7.58701423e-03, -1.09423190e-01,
        -7.93765634e-02, -1.95755720e-01, -1.90979242e-02, -2.09489778e-01,
         2.47414112e-02,  4.19138297e-02, -5.28238639e-02, -2.32324705e-01,
         8.30572750e-03, -1.16548873e-02, -1.54799148e-02,  4.90930304e-02,
         4.07092012e-02, -2.24016514e-02, -5.84624615e-03, -7.26676732e-02,
        -3.05888001e-02,  3.56669836e-02,  5.36373351e-03,  3.70354094e-02,
        -3.00989989e-02, -1.54267862e-01,  1.77055262e-02,  2.74378899e-03,
        -8.77451152e-04, -3.39035690e-02,  2.34820712e-02, -7.58502446e-03,
         9.07757040e-03, -2.38958467e-03, -3.04873195e-03, -3.43019329e-03,
         1.90302264e-02, -1.12659484e-02, -6.55687414e-03,  2.42341477e-02,
  